In [4]:
# !pip3 install https://github.com/casper-hansen/AutoAWQ/releases/download/v0.1.8/autoawq-0.1.8+cu118-cp310-cp310-linux_x86_64.whl

In [5]:
from awq import AutoAWQForCausalLM
from transformers import AutoConfig, AwqConfig, AutoTokenizer, AutoModelForCausalLM
import torch

model_path = 'mesolitica/mallam-1.1b-20k-instructions-rag'

In [6]:
model = AutoModelForCausalLM.from_pretrained(model_path, torch_dtype = torch.bfloat16)

config.json:   0%|          | 0.00/655 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/2.25G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/111 [00:00<?, ?B/s]

In [7]:
model.save_pretrained('./test', safe_serialization = False)

In [8]:
model = AutoAWQForCausalLM.from_pretrained('./test')

In [9]:
quant_path = 'mallam-1.1b-20k-instructions-rag-awq'
quant_config = { "zero_point": True, "q_group_size": 128, "w_bit": 4, "version": "GEMM" }

tokenizer = AutoTokenizer.from_pretrained(model_path, trust_remote_code=True)
model.quantize(tokenizer, quant_config=quant_config, calib_data = 'mesolitica/malaysian-calibration')

tokenizer_config.json:   0%|          | 0.00/1.69k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.34M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/638 [00:00<?, ?B/s]

Generating train split: 0 examples [00:00, ? examples/s]

AWQ: 100%|██████████| 22/22 [02:28<00:00,  6.75s/it]


In [10]:
model.save_quantized(quant_path, safetensors = False)
tokenizer.save_pretrained(quant_path)

('mallam-1.1b-20k-instructions-rag-awq/tokenizer_config.json',
 'mallam-1.1b-20k-instructions-rag-awq/special_tokens_map.json',
 'mallam-1.1b-20k-instructions-rag-awq/tokenizer.json')

In [12]:
tokenizer.push_to_hub('mesolitica/mallam-1.1b-20k-instructions-rag-AWQ')

CommitInfo(commit_url='https://huggingface.co/mesolitica/mallam-1.1b-20k-instructions-rag-AWQ/commit/ef848a832fb7b21f0bf4b808a83af300ed07beca', commit_message='Upload tokenizer', commit_description='', oid='ef848a832fb7b21f0bf4b808a83af300ed07beca', pr_url=None, pr_revision=None, pr_num=None)

In [13]:
quantization_config = AwqConfig(
    bits=quant_config['w_bit'],
    group_size=quant_config['q_group_size'],
    zero_point=quant_config['zero_point'],
    backend='autoawq',
    version=quant_config['version'].lower(),
)

config = AutoConfig.from_pretrained(model_path)
config.quantization_config = quantization_config

config.push_to_hub('mesolitica/mallam-1.1b-20k-instructions-rag-AWQ')

CommitInfo(commit_url='https://huggingface.co/mesolitica/mallam-1.1b-20k-instructions-rag-AWQ/commit/40c9e6295642ca0e5cdc4b8ff8888a73c1ce25d3', commit_message='Upload config', commit_description='', oid='40c9e6295642ca0e5cdc4b8ff8888a73c1ce25d3', pr_url=None, pr_revision=None, pr_num=None)

In [16]:
!ls mallam-1.1b-20k-instructions-rag-awq

config.json		quant_config.json	 tokenizer_config.json
generation_config.json	special_tokens_map.json
pytorch_model.bin	tokenizer.json


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


In [14]:
from huggingface_hub import HfApi

api = HfApi()

In [17]:
api.upload_file(
    path_or_fileobj='mallam-1.1b-20k-instructions-rag-awq/pytorch_model.bin',
    path_in_repo="pytorch_model.bin",
    repo_id='mesolitica/mallam-1.1b-20k-instructions-rag-AWQ',
    repo_type="model",
)

pytorch_model.bin:   0%|          | 0.00/778M [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/mesolitica/mallam-1.1b-20k-instructions-rag-AWQ/commit/4caae4a226e3dd569ac467c5099cd159ac5fa3e0', commit_message='Upload pytorch_model.bin with huggingface_hub', commit_description='', oid='4caae4a226e3dd569ac467c5099cd159ac5fa3e0', pr_url=None, pr_revision=None, pr_num=None)

In [18]:
api.upload_file(
    path_or_fileobj='mallam-1.1b-20k-instructions-rag-awq/quant_config.json',
    path_in_repo="quant_config.json",
    repo_id='mesolitica/mallam-1.1b-20k-instructions-rag-AWQ',
    repo_type="model",
)

CommitInfo(commit_url='https://huggingface.co/mesolitica/mallam-1.1b-20k-instructions-rag-AWQ/commit/81a4cf5cdf2ecd38d74354f558af0d2896a24b7d', commit_message='Upload quant_config.json with huggingface_hub', commit_description='', oid='81a4cf5cdf2ecd38d74354f558af0d2896a24b7d', pr_url=None, pr_revision=None, pr_num=None)

In [19]:
quantized_model = AutoModelForCausalLM.from_pretrained('mesolitica/mallam-1.1b-20k-instructions-rag-AWQ')
_ = quantized_model.cuda()


config.json:   0%|          | 0.00/909 [00:00<?, ?B/s]

You have loaded an AWQ model on CPU and have a CUDA device available, make sure to set your model on a GPU device in order to run your model.


pytorch_model.bin:   0%|          | 0.00/778M [00:00<?, ?B/s]

In [23]:
messages = [
    {'role': 'user', 'content': 'kwsp tu apa'}
]
tokenizer.apply_chat_template(messages, tokenize = False)

'<s>[INST] kwsp tu apa [/INST]'

In [26]:
messages = [
    {'role': 'user', 'content': 'KWSP tu apa?'}
]
prompt = tokenizer.apply_chat_template(messages, tokenize = False)
inputs = tokenizer([prompt], return_tensors='pt', add_special_tokens=False).to('cuda')

In [27]:
%%time

generate_kwargs = dict(
    inputs,
    max_new_tokens=1024,
    top_p=0.95,
    top_k=50,
    temperature=0.9,
    do_sample=True,
    num_beams=1,
)
r = quantized_model.generate(**generate_kwargs)
tokenizer.decode(r[0])

Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


CPU times: user 4.65 s, sys: 3.73 ms, total: 4.65 s
Wall time: 4.65 s


'<s> [INST] KWSP tu apa? [/INST]Kumpulan Wang Simpanan Pekerja (KWSP) atau EPF adalah tabung simpanan wang pekerja di Malaysia. KWSP ialah institusi keselamatan sosial yang disediakan oleh kerajaan Malaysia untuk membantu pekerja Malaysia menguruskan dana persaraan mereka.\n\nKWSP bertujuan untuk menyediakan sumber kewangan untuk membantu pekerja Malaysia melabur dan menyimpan untuk masa depan mereka. Ia mempunyai objektif utama untuk mencapai matlamat ini, iaitu memastikan ahli KWSP mempunyai simpanan yang mencukupi untuk memenuhi keperluan persaraan mereka.\n\nKWSP menyediakan faedah persaraan yang berbeza, seperti KWSP Prihatin dan KWSP i-Sinar. Simpanan KWSP yang dikhaskan boleh digunakan untuk tujuan yang berbeza, seperti membiayai pendidikan anak-anak, membeli rumah, atau memenuhi keperluan perubatan.\n\nSecara amnya, ahli KWSP layak untuk pelbagai jenis manfaat persaraan yang mereka boleh perolehi, bergantung pada umur, tahap kecacatan, dan sektor pekerjaan mereka. Ini termasuk 